# Notebook de Análise

Esse é o primeiro de múltiplos notebooks que irei desenvolver para o case. Os motivos da divisão são facilitar a leitura e organização. Os notebooks estarão numerados para declarar um sentido de ordem de leitura/entendimento do que executei e serve para representar minha linha de pensamentos. Adicionalmente, pretendo anotar dúvidas e observações que apareçam durante a execução e possíveis respostas que venha a obter.

Como uma forma de seguir guidelines, irei listar aqui os pontos de atenção que imagino que devam ser respondidos:

    - Existe algum padrão no comportamento dos fraudadores?
    - Esse dataset é suficiente para tirar alguma conclusão?
    - Conseguimos fazer alguma “feature engineering” que nos auxilie a identificar os
    fraudadores?
    - Como poderíamos identificá-los antes das denúncias?
    - Consegue propor alguma sugestão do que é necessário ser feito para solucionar o
    problema?

A resposta que devo, obrigatoriamente, responder:  

    Além de fraudes de boleto, quais são outros riscos que o mercado de adquirência está exposto e como
    poderíamos tentar mitigá-los?

Sem mais nada a adicionar, sigo para a análise.


## Entendimento do problema

O Pagar.me é uma adquirente e seu papel é [capturar, processar e liquidar um pagamento](https://pagar.me/blog/como-as-transacoes-sao-processadas-no-mercado-de-pagamento/), ou seja, é a responsável por fazer a comunicação entre outros agentes que participam do processo de uma compra. Uma adquirente fornece diversas formas de pagamento para que uma loja possa atender seus clientes (Cartão de Crédito, Boleto, Cartão de Débito, Voucher e Pix). O Pagar.me possui um sistema [antifraude](https://pagar.me/blog/antifraude-para-ecommerce/) em funcionamento, que é responsável por identificar compradores que possam estar tentando fraudar alguma compra. No entanto, o problema ocorre nos pagamentos de boletos fraudulentos, caso que aparentemente não é coberto pelo antifraude.

Pelo que compreendi dos mecanismos desse tipo de fraude elas ocorrem na emissão de boletos se passando por outros beneficiários e que depois são enviados à consumidores que desatentamente pagam os boletos falsos. O dinheiro então é entregue ao cliente fraudulento ou estornado para uma conta bancária que não é a do pagador. O que se deseja aqui é identificar o comportamento de clientes fraudadores que emitem boletos falsificados e evitar prejuízo ao consumidor e ao Pagar.me, mas isso precisa ocorrer antes das denúncias, logo, antes de ocorrerem os pagamentos/estornos indevidos. 

Objetivos:
- Identificar padrão dos fraudadores com os dados fornecidos
- Testar estratégias e determinar factibilidade de identificação de fraudadores com os dados fornecidos
- Tentar propor alguma solução para identificar fraudadores antes das denúncias

## Imports

In [1]:
import pandas as pd
import plotly.express as px
import plotly.io as pio
import plotly.graph_objects as go
import matplotlib.pyplot as plt
import seaborn as sns
from datetime import datetime
import numpy as np
import scipy.stats as stats
from sklearn.metrics import silhouette_score

sns.set_theme(
    style='whitegrid',
    context='notebook',
    palette='dark',
    font='Segoe UI',
    font_scale=1.5,
    rc={
        'figure.figsize': (12, 8),
    }
)

pio.templates.default = 'plotly_dark'
pio.renderers.default = 'png'

## Análise exploratória e entendimento dos dados

### Carregamento dos dados

Primeiro dos questionamentos: existe alguma diferença entre os arquivos `.csv` e `.xlsx`?

In [2]:
data = pd.read_excel(
    'dataset_case_boleto (4).xlsx',
    )

In [3]:
data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 9277 entries, 0 to 9276
Data columns (total 14 columns):
 #   Column                Non-Null Count  Dtype  
---  ------                --------------  -----  
 0   mes_ref               9277 non-null   int64  
 1   company_id            9277 non-null   object 
 2   tipo_doc              9277 non-null   object 
 3   max_valor_boleto      9277 non-null   float64
 4   avg_valor_boleto      9277 non-null   float64
 5   total_valor_boleto    9277 non-null   float64
 6   valor_boleto_stdv     9277 non-null   float64
 7   qtd_boleto_pago       9277 non-null   int64  
 8   qtd_boleto_total      9277 non-null   int64  
 9   qtd_boleto_estorno    9277 non-null   int64  
 10  qnt_cc_total          9277 non-null   int64  
 11  tempo_credenciamento  9277 non-null   int64  
 12  conta_bnk_repetida    9277 non-null   int64  
 13  fraude                9277 non-null   int64  
dtypes: float64(4), int64(8), object(2)
memory usage: 1014.8+ KB


Não parecem existir linhas consideradas nulas. Ainda assim, irei checar campo a campo.

In [4]:
data.head()

mes_ref                company_id tipo_doc  max_valor_boleto  \
0    43891  5e74d202d1498c5bdf8aafe3     cnpj            6000.0   
1    43891  5e78dafeb5ac867c7e85eb5e     cnpj            1800.0   
2    43891  5e73e21359193c2f123c1076     cnpj             159.9   
3    43922  5e7262c49d55ea5dbea59d57     cnpj             600.0   
4    43922  5e610d9f66945c0f82dd357f     cnpj            2941.0   

   avg_valor_boleto  total_valor_boleto  valor_boleto_stdv  qtd_boleto_pago  \
0           4884.61             63500.0            2122.83               10   
1           1800.00              3600.0               0.00                0   
2            104.90               209.8              77.78                0   
3            600.00              1800.0               0.00                0   
4           1764.60              8823.0             657.63                2   

   qtd_boleto_total  qtd_boleto_estorno  qnt_cc_total  tempo_credenciamento  \
0                13                   0            35                    11   
1                 2                   0             0                    11   
2                 2                   0            14                    11   
3                 3                   0            18                    11   
4                 5                   0            65                    12   

   conta_bnk_repetida  fraude  
0                   0       0  
1                   0       0  
2                   0       0  
3                   0       0  
4                   0       0

Com essa amostra vejo que existe alguma inconsistência entre o dicionário e o conjunto de dados. Os campos `max_valor_boleto`, `avg_valor_boleto`, `total_valor_boleto` e `valor_boleto_stdv` estão como float64 e existem números com casas decimais. No dicionário os dados são definidos como discretos. Seria esse um equívoco na definição do dicionário ou na representação dos dados? Tirar dúvida sobre isso. No momento irei tratar os dados como dados contínuos pois, pelo nome dos campos, faz sentido que sejam números reais por se tratar de totais, médias e valores.

Outro ponto é: sei qual é minha variável alvo e, portanto, é possível fazer a análise dos campos observando a relação com o campo `fraude`.

### Análise campo a campo

### company_id

Primeiramente, verifico se existe alguma forma de repetição de valores no campo `company_id`.

In [5]:
data.company_id.value_counts()

5e1c738d7268a016d9e71108    14
5e7deeb02f762855a6cda76f    13
5e8248b696d2ac227249d8ac    13
5e7cbc38f2eebc591d523154    13
5e73911df84ce3362c22ae23    13
                            ..
5e8bdf6e97aeba54644ed5be     1
5fbc451a9ab2b9001641ca01     1
601eb0e5a1bff400115c4ff3     1
60255ac95f9809001231690f     1
5fc3ed1659018400162a83ad     1
Name: company_id, Length: 4960, dtype: int64

Como é possível ver, existem 4960 clientes distintos no campo `company_id`. Dessa forma, do ponto de vista de análise do problema, tenho 4960 clientes para analisar como fraudadores ou não. Isso me dá a possibilidade de fazer uma detecção de clientes fraudadores com base na criação do perfil de um cliente. No entanto, a criaçao de um novo conjunto contendo apenas o perfil viria com a perda de informação dos clientes ao criar as medidas. Dessa forma, tomo a decisão de manter a base como está por alguns motivos:

- A detecção de fraudadores é uma tarefa que deve ser feita constantemente e baseá-la em um perfil pode deteriorar o desempenho do modelo de detecção pelo ruído gerado em casos de clientes regulares que se tornaram fraudadores, por exemplo. Um ponto que talvez venha a ser vantajoso é a possível detecção de padrão de fraude antes que algum dano seja causado.
- Existe um problema de continuidade nos dados presentes na base. Alguns clientes possuem dados de meses que não são contínuos. Irei desconsiderar essa informação visto que criar medidas e aplicá-las aos clientes ficaria muito complexo levando isso em conta.

#### fraude

Esse é o campo alvo do case.

In [6]:
data.fraude.value_counts()

0    7683
1    1594
Name: fraude, dtype: int64

Num primeiro momento não observo nada de estranho na contagem dos valores. Para facilitar a criação e tratamento da visualização, irei criar uma variável para converter os valores para booleanos.

In [7]:
data['fraude_bool'] = data.fraude.astype('bool')

Antes de visualizar quantos clientes são fraudadores e quantos não são, verifico se existe alguma contaminação dos dados.

In [8]:
set_fraude = set(data.query('fraude_bool == True').company_id.unique())
set_regular = set(data.query('fraude_bool == False').company_id.unique().tolist())
set_fraude_regular = set_fraude.intersection(set_regular)
set_fraude_regular

set()

In [9]:
fraud_by_client_count = data.groupby('fraude_bool').company_id.nunique().to_frame()
fraud_by_client_count

company_id
fraude_bool            
False              3792
True               1168

O set vazio indica que não eixstem clientes em situação ambígua na base.

In [10]:
px.bar(
    fraud_by_client_count,
    color=fraud_by_client_count.index,
    labels={'fraude_bool': 'Fraudulento?',},
    title='Situação dos Clientes',
    text_auto=True
).update_layout(
    yaxis_title='Quantidade de Clientes',
    )

Dessa forma, é possível ver que a maior parte, dos clientes está dentro da normalidade até o momento da extração desses dados. Um ponto importante para lembrar é que um cliente fraudulento é marcado como fraudulento em todos os meses do registro. Isso pode gerar ruídos para os modelos.

#### mes_ref

Antes de qualquer coisa, uma contagem simples de valores para avaliar alguma inconsistência que possa passar despercebida.

In [11]:
data.mes_ref.value_counts()

44228    1423
44197    1027
44166     817
44136     792
44013     771
43983     739
44044     680
44075     679
43952     649
44105     638
44256     443
43922     420
43891     174
43862      17
43831       8
Name: mes_ref, dtype: int64

Os dados foram carregados a partir do excel e seu formato de data vem como um inteiro que significa a contagem de dias a partir de uma data de referência.

In [12]:
def int_to_datetime(x: int) -> datetime:
    return datetime.fromordinal(datetime(1900, 1, 1).toordinal() + x - 2)


In [13]:
data.mes_ref = data.mes_ref.apply(int_to_datetime)

In [14]:
data.mes_ref.value_counts()

2021-02-01    1423
2021-01-01    1027
2020-12-01     817
2020-11-01     792
2020-07-01     771
2020-06-01     739
2020-08-01     680
2020-09-01     679
2020-05-01     649
2020-10-01     638
2021-03-01     443
2020-04-01     420
2020-03-01     174
2020-02-01      17
2020-01-01       8
Name: mes_ref, dtype: int64

As contagens se mantêm. As datas, como no nome, fazem referência a um mês. O dia, além de não mudar nos dados, não é relevante para a análise.

In [15]:
px.histogram(
    data, 
    x='mes_ref', 
    title='Situação dos Clientes por Mês de Referência', 
    color='fraude_bool', 
    text_auto=True, 
    labels={
        'mes_ref': 'Mês de Referência', 
        'fraude_bool': 'Fraudulento?'}, 
    barmode='group'
    ).update_layout(
        yaxis_title='Quantidade de Clientes',
        )

**Aqui faz sentido que exista um aumento de irregularidades no período entre outubro e março**. Existem diversos eventos ocorrendo nesse intervalo: Black Friday em novembro, natal em dezembro, ano novo em janeiro e carnaval em fevereiro.

Quanto ao ano, não vejo muita utilidade em manter como informação para um modelo. Os dados do começo de 2020 são escassos e não possuem indicações de fraude, não trazem muita informação por serem pouco representativos em relação ao resto. E o mais importante: os eventos que podem trazer um pico de atividade fraudulenta se repetem ano a ano e não exclusivamente no ano de 2020 ou 2021. Portanto, além do dia, provavelmente irei descartar a informação do ano.

No próximo gráfico observo a situação mais recente de cada cliente e verifico se existe alguma diferença no padrão.

In [16]:
px.histogram(
    data.groupby('company_id').max(),
    x='mes_ref', 
    title='Situação de Clientes por Mês de Referência Mais Recente',
    color='fraude_bool', 
    text_auto=True, 
    labels={
        'mes_ref': 'Mês de Referência', 
        'fraude_bool': 'Fraudulento?'}, 
    barmode='group'
    ).update_layout(
        yaxis_title='Quantidade de Clientes',
        )

Olhando para os meses mais recentes de cada cliente observo que a tendência não mudou apesar da redução da quantidade em cada barra, visto que os meses anteriores de cada cliente foram removidos da visualização.

Crio, então, uma nova coluna contendo somente o nome do mês de referência:

In [17]:
data['nome_mes_ref'] = data.mes_ref.dt.month_name()

In [18]:
month_names = ['January', 'February', 'March', 'April', 'May', 'June', 'July', 'August', 'September', 'October', 'November', 'December']
px.histogram(
    data, 
    x='nome_mes_ref', 
    title='Contagem de Cliente por Mês de Referência', 
    color='fraude_bool', text_auto=True, 
    labels={'nome_mes_ref': 'Mês de Referência', 'fraude_bool': 'Fraude?'},
    barmode='group',
    category_orders={
        'nome_mes_ref': month_names
    })

A visualização permanece praticamente a mesma, com o pico de atividade fraudulenta nos limites entre um ano e outro.

Para o próximo campo irei pular a ordem e analisar o `tempo_credenciamento` para avaliar a relação do campo com os meses e o campo fraude.

### tempo_credenciamento

Esse campo tem potencial de mostrar uma relação que acredito ser importante se relacionada entre o mês de referência e ao campo fraude.

In [19]:
data.tempo_credenciamento.value_counts()

11    2071
0     1850
10    1202
9      965
1      673
8      463
4      389
3      337
2      314
5      281
6      261
7      222
12     141
14      54
13      54
Name: tempo_credenciamento, dtype: int64

Observo aqui um caso particular de contas com 0 meses de tempo de credenciamento. Penso que são contas recém criadas.

Agora uma visualização para verificar a distribuição desses valores. Nessas visualizações irei usar os registros mais recentes de cada cliente pois os valores de tempo de credenciamento só contam quando o cliente está em vigência na base, então quando o cliente comete uma fraude, o tempo de credenciamento para de crescer. Ainda, os valores de indicação de fraude são os mesmos em todos os meses do registro.

In [20]:
px.histogram(
    data.groupby('company_id').max(),
    x='tempo_credenciamento',
    title='Situação de Clientes por Tempo de Credenciamento',
    color='fraude_bool',
    text_auto=True,
    labels={'tempo_credenciamento': 'Tempo de Credenciamento', 'fraude_bool': 'Fraudulento?'},
    barmode='group'
).update_layout(
    yaxis_title='Quantidade de Clientes',
    )

Na visualização, vemos que clientes fraudulentos se concentram muito em um lado do histograma -- contas com menor tempo de credenciamento. Existem alguns poucos casos em contas com maiores tempos de casa. Quanto à distribuição, no geral, os clientes se dividem entre clientes muito novos e outros com um tempo consideravelmente maior de casa.

Para melhor observar a distribuição desses dados, irei criar uma boxplot.

In [21]:
px.box(
    data.groupby('company_id').max(),
    x='tempo_credenciamento',
    # y='fraude_bool',
    title='Boxplot do Tempo de Credenciamento',
    color='fraude_bool',
    labels={'tempo_credenciamento': 'Tempo de Credenciamento', 'fraude_bool': 'Fraudulento?'},
)

In [22]:
px.ecdf(
    data.groupby('company_id').max().query('fraude_bool == True'),
    x='tempo_credenciamento',
    title='Frequência Cumulativa de Fraudes por Tempo de Credenciamento',
    labels={'tempo_credenciamento': 'Tempo de Credenciamento'},
).update_layout(
    yaxis_title='Frequência Cumulativa',
    )

De forma clara é visto que os clientes fraudulentos tem um tempo de credenciamento mais localizado e menor que os clientes não fraudulentos. No caso onde ocorreram fraudes, 63% dos clientes tem tempo de credenciamento menor que 1 mês, 86% possuem até 2 meses de credenciamento e o restante até 9 meses. A boxplot considera os casos de fraude acima de 2 meses como outliers, cerca de 6%. Ainda assim, existe aqui um padrão no comportamento dos clientes fraudulentos: fraudes ocorrem em contas com menor tempo de credenciamento, particularmente naquelas recém credenciadas.

Seria possível seria possível dizer que uma forma de mitigar isso seria com alguma estratégia de bloqueio/filtro de transações ou ações de clientes recentemente credenciados (<= 3 meses), mas é verificado que clientes com maior tempo de credenciamento também cometem fraudes. O que proponho é a análise mês a mês de cada cliente. Com a criação de novas *features* para os dados pode ser possível passar o comportamento do cliente para o modelo ao longo dos meses.

### conta_bnk_repetida

Segundo o dicionário, esse é um campo que indica se a conta bancária informada para estorno já foi usada anteriormente em outras contas pagar.me. Pelo que se entende do problema as fraudes ocorrem por boletos. 

Segundo a [página de suporte](https://pagarme.helpjuice.com/p1-transa%C3%A7%C3%B5es-e-estornos/estorno-%7C-como-estornar-uma-transa%C3%A7%C3%A3o?from_search=89283143) quando uma transação via boleto é estornada, uma transferência bancária é feita para a conta informada. Um caminho que vejo aqui para que se justifique a existência desse campo é a emissão de um boleto fraudulento que é pago por um cliente desavisado. Mas se existe a transferência direta, qual o papel dessa informação nas fraudes? Pretendo tirar essa dúvida e analisar os campos.

Segundo a dúvida tirada: a conta informada para estorno deveria ser a do consumidor que está pagando o boleto, mas no caso de boletos fraudulentos, a conta informada para estorno é de um titular diferente do que está pagando o boleto.

In [23]:
data.conta_bnk_repetida.value_counts()

0    8282
1     995
Name: conta_bnk_repetida, dtype: int64

Não observo nenhum valor nulo no campo. Irei dar o mesmo tratamento que dei ao campo `fraude`, transformar em booleanos.

In [24]:
data['conta_bnk_repetida_bool'] = data.conta_bnk_repetida.astype('bool')

In [25]:
data.groupby(
    'conta_bnk_repetida').company_id.nunique().to_frame()
set_conta_bnk_repetida = set(data.query(
    'conta_bnk_repetida_bool == True').company_id.unique())
set_conta_bnk_nao_repetida = set(data.query(
    'conta_bnk_repetida_bool == False').company_id.unique())
set_conta_bnk_repetida_nao_repetida = set_conta_bnk_repetida.intersection(
    set_conta_bnk_nao_repetida)
set_conta_bnk_repetida_nao_repetida

set()

Esse campo não apresente nenhuma ambiguidade para os clientes. Talvez tenha sido marcado em todos os meses de referência assim como o campo `fraude`.

Para a visualização desse campo também irei usar os dados mais recentes de cada cliente.

In [26]:
px.histogram(
    data.groupby('company_id').max(),
    x='fraude_bool',
    color='conta_bnk_repetida_bool',
    text_auto=True,
    title='Contas Repetidas por Fraude',
    labels={
        'conta_bnk_repetida_bool': 'Conta Repetida?',
        'fraude_bool': 'Fraudulento?'
        },
    barmode='group',
).update_layout(
    yaxis_title='Quantidade de Clientes',
    )

In [27]:
px.pie(
    data.groupby('company_id').max().query('fraude_bool == True'),
    # values='conta_bnk_repetida_bool',
    names='conta_bnk_repetida_bool',
    title='Contas Repetidas por Fraude',
    # text_auto=True,
    labels={
        'conta_bnk_repetida_bool': 'Conta Repetida?',
        'fraude_bool': 'Fraudulento?'
        },
)

Com esse campo observa-se que clientes que cometem fraudes usam mais frequentemente contas para estorno repetidas do que clientes que não cometeram fraudes. Em outras palavras: um cliente que usa uma conta repetida tem mais chances de ser um cliente fraudulento do que um cliente que não informou uma conta repetida.

### tipo_doc

Essa variável informa se o documento informado é CPF ou CNPJ.

In [28]:
data.tipo_doc.value_counts()

cpf     4726
cnpj    4551
Name: tipo_doc, dtype: int64

Nenhum dado vazio. 

Também irei usar os dados mais recentes para a visualização visto que esses não são afetados pela variação do tempo.

In [29]:
px.histogram(
    data.groupby('company_id').max(),
    x='fraude_bool',
    color='tipo_doc',
    text_auto=True,
    title='Fraudes por tipo de documento',
    labels={
        'tipo_doc': 'Tipo de Documento',
        'fraude_bool': 'Fraudulento?'
        },
    barmode='group',
).update_layout(
    yaxis_title='Quantidade de Clientes',
    )

In [30]:
px.pie(
    data.groupby('company_id').max().query('fraude_bool == True'),
    names='tipo_doc',
    title='Tipo de Documento usado por Clientes Fraudulentos',
    labels={'tipo_doc': 'Tipo de Documento'},
)

O que se observa aqui é que clientes fraudulentos são mais propensos a usar documentos CPF do que CNPJ.

### max_valor_boleto

Valor máximo de um boleto transacionado por um cliente em reais. Aqui espero encontrar algum tipo de relação entre o valor e um cliente fraudulento.

In [31]:
data.max_valor_boleto.describe()

count    9.277000e+03
mean     1.364116e+04
std      3.073980e+05
min      1.000000e+00
25%      1.600000e+02
50%      5.202000e+02
75%      4.463680e+03
max      2.147484e+07
Name: max_valor_boleto, dtype: float64

In [32]:
px.histogram(
    data,
    x='max_valor_boleto',
    title='Histograma do Valor Máximo Transacionado em Boleto para a base de dados',
    labels={'max_valor_boleto': 'Valor Máximo Transacionado em Boleto', 'fraude_bool': 'Fraude?'},
).update_layout(
    yaxis_title='Quantidade',
    )

In [33]:
px.box(
    data,
    x='max_valor_boleto',
    color='fraude_bool',
    title='Distribuição do Valor Máximo Transacionado em Boleto por Situação do Cliente',
    labels={'max_valor_boleto': 'Valor Máximo Transacionado em Boleto',
            'fraude_bool': 'Fraudulento?'},
)


Os dados desse atributo apresentam distribuição muito assimétrica. A esparsidade da distribuição é muito alta e os casos mais extremos parecem ter origem em uma distribuição diferente. É possível ver que a distribuição dos tipos de clientes difere bastante. O espalhamento das duas boxes é diferente, com os clientes não fraudulentos estando localizados no começo do histograma -- entre 1 e 2950 reais. Já os clientes fraudulentos transacionam boletos de até 67mil. O posicionamento da mediana está muito distante entre as duas boxes.

In [34]:
stats.mannwhitneyu(
    data.query('fraude_bool == True').max_valor_boleto,
    data.query('fraude_bool == False').max_valor_boleto
)

MannwhitneyuResult(statistic=10870553.5, pvalue=0.0)

O teste de hipótese me leva a concluir que existe uma diferença significativa entre as medianas de um cliente fraudulento e um cliente regular ao rejeitar a hipótese nula (p < 0.05) de que as medianas das duas distribuições são iguais.

Crio um agrupamento dos dados de acordo com o identificador do cliente. 

In [35]:
company_gb = data.groupby('company_id')

Agora crio um novo atributo e o coloco em todos os meses de cada cliente do agrupamento. Dessa forma um valor comum é compartilhado por todos esses campos.

In [36]:
data['mean_max_valor_boleto'] = 0
data['median_max_valor_boleto'] = 0
data['std_max_valor_boleto'] = 0
for company_id in data.company_id.unique():
    selector = data.company_id == company_id
    data.loc[selector, 'mean_max_valor_boleto'] = company_gb.get_group(company_id).max_valor_boleto.mean()
    data.loc[selector, 'median_max_valor_boleto'] = company_gb.get_group(company_id).max_valor_boleto.median()
    data.loc[selector, 'std_max_valor_boleto'] = company_gb.get_group(company_id).max_valor_boleto.std(ddof=0)


### avg_valor_boleto

Valor médio de boletos transacionados na conta do cliente no mês de referência.

In [37]:
data.avg_valor_boleto.describe()

count    9.277000e+03
mean     6.102405e+03
std      1.390150e+05
min      1.000000e+00
25%      1.315000e+02
50%      3.388800e+02
75%      2.123420e+03
max      1.123742e+07
Name: avg_valor_boleto, dtype: float64

In [38]:
px.histogram(
    data,
    x='avg_valor_boleto',
    title='Histograma do Valor Médio Transacionado em Boleto',
    labels={'avg_valor_boleto': 'Valor Médio Transacionado em Boleto'},
).update_layout(
    yaxis_title='Quantidade',
    )


In [39]:
px.box(
    data,
    x='avg_valor_boleto',
    color='fraude_bool',
    title='Distribuição do Valor Médio Transacionado em Boleto por Situação do Cliente',
    labels={'avg_valor_boleto': 'Valor Médio Transacionado em Boleto',
            'fraude_bool': 'Fraudulento?'},
)

In [40]:
stats.mannwhitneyu(
    data.query('fraude_bool == True').avg_valor_boleto,
    data.query('fraude_bool == False').avg_valor_boleto
)

MannwhitneyuResult(statistic=10718769.0, pvalue=0.0)

Essa também é uma distribuição onde existe uma diferença significativa entre o comportamento de um cliente fraudulento e um cliente regular quanto aos valores médios de um boleto transacionado em suas contas. Não irei criar medidas para esse campo. O erro inserido por duas médias é muito grande.

### total_valor_boleto

Valor total transacionado em boletos no período.

In [41]:
data.total_valor_boleto.describe()

count    9.277000e+03
mean     2.772717e+04
std      3.235246e+05
min      1.000000e+00
25%      2.682000e+02
50%      1.489000e+03
75%      1.068454e+04
max      2.247484e+07
Name: total_valor_boleto, dtype: float64

In [42]:
px.histogram(
    data,
    x='total_valor_boleto',
    title='Histograma do Valor Total Transacionado em Boleto',
    labels={'total_valor_boleto': 'Valor Total Transacionado em Boleto'},
).update_layout(
    yaxis_title='Quantidade',
)

In [43]:
px.box(
    data,
    x='total_valor_boleto',
    color='fraude_bool',
    title='Distribuição do Valor Total Transacionado em Boleto por Situação do Cliente',
    labels={'total_valor_boleto': 'Valor Total Transacionado em Boleto',
            'fraude_bool': 'Fraudulento?'},
)

In [44]:
stats.mannwhitneyu(
    data.query('fraude_bool == True').total_valor_boleto,
    data.query('fraude_bool == False').total_valor_boleto
)

MannwhitneyuResult(statistic=10791860.0, pvalue=0.0)

O comportamento aqui é distinto como em todos os outros campos. Os clientes fraudulentos tendem a transacionar um valor maior num curto período de tempo. Isso é condizente com o visto em outros campos: clientes fraudulentos tendem a ter menos tempo de casa, a transacionar valores máximos maiores e a emitir mais boletos.

Para esse campo crio a média do total transacionado em todos os meses de referência.

In [45]:
data['mean_total_valor_boleto'] = 0
data['median_total_valor_boleto'] = 0
data['std_total_valor_boleto'] = 0
for company_id in data.company_id.unique():
    selector = data.company_id == company_id
    data.loc[selector, 'mean_total_valor_boleto'] = company_gb.get_group(company_id).total_valor_boleto.mean()
    data.loc[selector, 'median_total_valor_boleto'] = company_gb.get_group(company_id).total_valor_boleto.median()
    data.loc[selector, 'std_total_valor_boleto'] = company_gb.get_group(company_id).total_valor_boleto.std(ddof=0)

### valor_boleto_stdv

Desvio padrão para os boletos transacionados no mês de referência.

In [46]:
data.valor_boleto_stdv.describe()

count    9.277000e+03
mean     4.973007e+03
std      1.921443e+05
min      0.000000e+00
25%      0.000000e+00
50%      3.809000e+01
75%      4.618800e+02
max      1.447790e+07
Name: valor_boleto_stdv, dtype: float64

In [47]:
px.histogram(
    data,
    x='valor_boleto_stdv',
    title='Histograma do Valor de Desvio Padrão Transacionado em Boleto',
    labels={'valor_boleto_stdv': 'Valor de Desvio Padrão Transacionado em Boleto'},
).update_layout(
    yaxis_title='Quantidade',
)

In [48]:
px.box(
    data,
    x='valor_boleto_stdv',
    color='fraude_bool',
    title='Distribuição do Valor de Desvio Padrão Transacionado em Boleto por Situação do Cliente',
    labels={'valor_boleto_stdv': 'Valor de Desvio Padrão Transacionado em Boleto',
            'fraude_bool': 'Fraudulento?'},     
)

In [49]:
stats.mannwhitneyu(
    data.query('fraude_bool == True').valor_boleto_stdv,
    data.query('fraude_bool == False').valor_boleto_stdv
)

MannwhitneyuResult(statistic=9687607.0, pvalue=0.0)

O mesmo padrão se repete aqui, mas dessa vez causado pelo espalhamento dos valores transacionados por clientes fraudulentos -- visível na boxplot de clientes fraudulentos. Os clientes fraudulentos movimentam boletos de valores mais variados do que clientes, como visto e evidenciado nas análises anteriores. Assim como o campo `avg_valor_boleto`, não irei criar uma nova medida sobre o desvio padrão.

### qtd_boleto_pago

Quantidade de boletos em que o último status é "pago".

In [50]:
data.qtd_boleto_pago.describe()

count    9277.000000
mean        4.499623
std        22.885944
min         0.000000
25%         0.000000
50%         1.000000
75%         2.000000
max       685.000000
Name: qtd_boleto_pago, dtype: float64

In [51]:
px.histogram(
    data,
    x='qtd_boleto_pago',
    title='Histograma da Quantidade de Boletos Pagos',
    labels={'qtd_boleto_pago': 'Quantidade de Boletos Pagos'},
).update_layout(
    yaxis_title='Quantidade',
    
)

In [52]:
px.box(
    data,
    x='qtd_boleto_pago',
    color='fraude_bool',
    title='Distribuição da Quantidade de Boletos Pagos por Situação do Cliente',
    labels={'qtd_boleto_pago': 'Quantidade de Boletos Pagos',
            'fraude_bool': 'Fraudulento?'},
)

In [53]:
stats.mannwhitneyu(
    data.query('fraude_bool == True').qtd_boleto_pago,
    data.query('fraude_bool == False').qtd_boleto_pago
)

MannwhitneyuResult(statistic=3895406.5, pvalue=1.7448739889918352e-128)

Considerando o intervalo de inter quartil, o cliente regular recebe pagamentos para no máximo 7 dos boletos emitidos enquanto o cliente fraudulento recebe 2. Até a diferença nos pontos considerados como outliers aqui é grande. Os clientes regulares chegam a ter 685 boletos pagos em um mês. O cliente irregular chega a apenas 31 boletos pagos. Existe aqui uma das maiores diferenças entre os clientes fraudulentos e os clientes regulares. Isso poderia ser causado por uma menor emissão de boletos, mas não é o caso. Credenciadas que cometem fraude emitem uma quantidade maior de boletos em um mês, mesmo que o único, do que uma credenciada regular normalmente faria.

Algumas medidas para compor o perfil do cliente:

In [54]:
data['max_qtd_boleto_pago'] = 0
data['mean_qtd_boleto_pago'] = 0

for company_id in data.company_id.unique():
    selector = data.company_id == company_id
    data.loc[selector, 'max_qtd_boleto_pago'] = company_gb.get_group(company_id).qtd_boleto_pago.max()
    data.loc[selector, 'mean_qtd_boleto_pago'] = company_gb.get_group(company_id).qtd_boleto_pago.mean()

### qtd_boleto_estorno

Quantidade de boletos em que o último status é "estornado".

In [55]:
data.qtd_boleto_estorno.describe()

count    9277.000000
mean        0.157917
std         0.876460
min         0.000000
25%         0.000000
50%         0.000000
75%         0.000000
max        25.000000
Name: qtd_boleto_estorno, dtype: float64

In [56]:
px.histogram(
    data,
    x='qtd_boleto_estorno',
    title='Histograma da Quantidade de Boletos Estornados',
    labels={'qtd_boleto_estorno': 'Quantidade de Boletos Estornados'},
).update_layout(
    yaxis_title='Quantidade',
)

In [57]:
px.box(
    data,
    x='qtd_boleto_estorno',
    color='fraude_bool',
    title='Distribuição da Quantidade de Boletos Estornados por Situação do Cliente',
    labels={'qtd_boleto_estorno': 'Quantidade de Boletos Estornados',
            'fraude_bool': 'Fraudulento?'},
)

In [58]:
stats.mannwhitneyu(
    data.query('fraude_bool == True').qtd_boleto_estorno,
    data.query('fraude_bool == False').qtd_boleto_estorno,
)

MannwhitneyuResult(statistic=7794963.0, pvalue=0.0)

O padrão de fraude aqui é quando um cliente fraudulento emite boletos com contas para estorno diferentes daquelas das pessoas que pagam o boleto e após isso o boleto é estornado para essa conta do fraudador. Entender isso dá sentido ao que é visto nos gráficos acima. O que é considerado normal para uma credenciada regular é nenhum estorno por mês. Para uma credenciada que emite boletos falsos, o estorno é mais frequente. O teste reforça essa diferença ao rejeitar a hipótese nula.

Para esse campo crio a medida de média, visto que pelo tempo de credenciamento um cliente fraudador tenderá a ter uma média maior que a de um cliente regular.

In [59]:
data['mean_qtd_boleto_estorno'] = 0

for company_id in data.company_id.unique():
    selector = data.company_id == company_id
    data.loc[selector, 'mean_qtd_boleto_estorno'] = company_gb.get_group(company_id).qtd_boleto_estorno.mean()

### qtd_boleto_total

Quantidade total de boletos emitidos no mês de referência.

In [60]:
data.qtd_boleto_total.describe()

count    9277.000000
mean       11.086774
std        40.794549
min         1.000000
25%         1.000000
50%         3.000000
75%         7.000000
max      1103.000000
Name: qtd_boleto_total, dtype: float64

In [61]:
px.histogram(
    data,
    x='qtd_boleto_total',
    title='Histograma da Quantidade Total de Boletos Emitidos',
    labels={'qtd_boleto_total': 'Quantidade Total de Boletos Emitidos'},
).update_layout(
    yaxis_title='Quantidade',
)

In [62]:
px.box(
    data,
    x='qtd_boleto_total',
    color='fraude_bool',
    title='Distribuição da Quantidade Total de Boletos Emitidos por Situação do Cliente',
    labels={'qtd_boleto_total': 'Quantidade Total de Boletos Emitidos',
            'fraude_bool': 'Fraudulento?'},
)

In [63]:
stats.mannwhitneyu(
    data.query('fraude_bool == True').qtd_boleto_total,
    data.query('fraude_bool == False').qtd_boleto_total
)

MannwhitneyuResult(statistic=8078320.0, pvalue=8.84470880855373e-94)

Clientes fraudadores emitem boletos mais frequentemente, mas não são os que tem mais boletos pagos mensalmente. Fraudadores geram uma quantidade alta de boletos que são amplamente distribuídos, pagos por alguns consumidores desavisados e então estornados para a conta do fraudador. Todo esse processo é condizente com o que é evidenciado pelos dados. No entanto, os maiores valores que uma credenciada alcança são de 1103 boletos emitido em um mês. Fazer uma média ou tirar um máximo poderia gerar ruído para o modelo ou levar um modelo a apontar uma credenciada regular como fraudulenta. Irei criar um total acumulado de boletos emitidos, que é a soma de todos os boletos emitidos em todos os meses.

In [64]:
data['sum_qtd_boleto_total'] = 0
for company_id in data.company_id.unique():
    selector = data.company_id == company_id
    data.loc[selector, 'sum_qtd_boleto_total'] = company_gb.get_group(company_id).qtd_boleto_total.sum()

Antes de concluir com esse campo crio um novo atributo de boletos não pagos, que são os boletos que não foram pagos ou estornados. Além disso calculo o percentual de boletos não pagos, pagos e estornados em relação ao total de boletos emitidos.

In [65]:
data['qtd_boleto_nao_pago'] = data.qtd_boleto_total - (data.qtd_boleto_pago + data.qtd_boleto_estorno)
data['rel_qtd_boleto_nao_pago'] = data.qtd_boleto_nao_pago / data.qtd_boleto_total
data['rel_qtd_boleto_estorno'] = data.qtd_boleto_estorno / data.qtd_boleto_total
data['rel_qtd_boleto_pago'] = data.qtd_boleto_pago / data.qtd_boleto_total

In [66]:
px.box(
    data,
    x='qtd_boleto_nao_pago',
    color='fraude_bool',
    title='Distribuição da Quantidade de Boletos Não Pagos por Situação do Cliente',
    labels={'qtd_boleto_nao_pago': 'Quantidade de Boletos Não Pagos',
            'fraude_bool': 'Fraudulento?'},
)


In [67]:
px.histogram(
    data,
    x='rel_qtd_boleto_nao_pago',
    color='fraude_bool',
    title='Distribuição da Frequência Relativa de Boletos Não Pagos por Situação do Cliente',
    labels={'rel_qtd_boleto_nao_pago': 'Frequência Relativa de Boletos Não Pagos',
            'fraude_bool': 'Fraudulento?'},
            marginal='box'
).update_layout(
    yaxis_title='Quantidade',
)

In [68]:
px.histogram(
    data,
    x='rel_qtd_boleto_estorno',
    color='fraude_bool',
    title='Distribuição da Frequência Relativa de Boletos Estornados por Situação do Cliente',
    labels={'rel_qtd_boleto_estorno': 'Frequência Relativa de Boletos Estornados',
            'fraude_bool': 'Fraudulento?'},
            marginal='box'
).update_layout(
    yaxis_title='Quantidade',
)

In [69]:
px.histogram(
    data,
    x='rel_qtd_boleto_pago',
    color='fraude_bool',
    title='Distribuição da Frequência Relativa de Boletos Pagos por Situação do Cliente',
    labels={'rel_qtd_boleto_pago': 'Frequência Relativa de Boletos Pagos',
            'fraude_bool': 'Fraudulento?'},
    marginal='box'
).update_layout(
    yaxis_title='Quantidade',
)

Com isso concluo que existe diferença entre as frequências relativas dos clientes. O cliente fraudulento tem mais boletos não pagos, estornados e menos boletos pagos que um cliente regular.

### qtd_cc_total

Quantidade de transações de cartão de crédito no mês de referência.

In [70]:
data.qnt_cc_total.describe()

count    9277.000000
mean        6.037728
std        18.828619
min         0.000000
25%         0.000000
50%         0.000000
75%         4.000000
max       528.000000
Name: qnt_cc_total, dtype: float64

In [71]:
px.histogram(
    data,
    x='qnt_cc_total',
    title='Histograma da Quantidade Total de Transações de Cartão de Crédito',
    labels={'qnt_cc_total': 'Quantidade Total de Transações de Cartões de Crédito'},
).update_layout(
    yaxis_title='Quantidade',
)

In [72]:
px.box(
    data,
    x='qnt_cc_total',
    color='fraude_bool',
    title='Distribuição da Quantidade Total de Transações de Cartões de Crédito por Situação do Cliente',
    labels={'qnt_cc_total': 'Quantidade Total de Transações de Cartões de Crédito',
            'fraude_bool': 'Fraudulento?'},
)

In [73]:
stats.mannwhitneyu(
    data.query('fraude_bool == True').qnt_cc_total,
    data.query('fraude_bool == False').qnt_cc_total
)

MannwhitneyuResult(statistic=3115111.5, pvalue=1.4262465627099232e-262)

Transações de cartão de crédito são feitas por clientes regulares mais frequentemente que os fraudulentos -- que quase não possuem transações desse tipo. O teste novamente rejeita a hipótese nula (p < 0.05) que as medianas das duas distribuições são iguais. Dado que o mecanismo que gera a fraude é feito através de emissão de boletos falsos, era esperado um comportamento de baixo volume de transações via cartão de crédito.

Como atributo construído a partir desse campo, crio um novo atributo que é a frequência relativas de transações de cartão de crédito em relação ao total de transações via boleto somadas ao total de transações de cartão de crédito.

In [74]:
data['freq_rel_cc_total_cc_boleto'] = data.qnt_cc_total / (data.qtd_boleto_total + data.qnt_cc_total)

In [75]:
px.histogram(
    data,
    x='freq_rel_cc_total_cc_boleto',
    color='fraude_bool',
    title='Distribuição da Frequência Relativa de Transações de Cartões de Crédito por Situação do Cliente',
    labels={'freq_rel_cc_total_cc_boleto': 'Frequência Relativa de Transações de Cartões de Crédito',
            'fraude_bool': 'Fraudulento?'},
            marginal='box'
)

In [76]:
stats.mannwhitneyu(
    data.query('fraude_bool == True').freq_rel_cc_total_cc_boleto,
    data.query('fraude_bool == False').freq_rel_cc_total_cc_boleto
)

MannwhitneyuResult(statistic=3109650.0, pvalue=2.0707466294691553e-263)

Esse campo parece diferenciar bem o cliente fraudulento do cliente regular. Vou mantê-lo como atributo.

## Considerações finais sobre a análise

Sobre os dados: são de boa qualidade, não precisei fazer nenhuma limpeza de dados ou correção de erros. Existe, porém, um tipo de problema na base -- em meu ponto de vista. Para alguns clientes os dados de `mes_ref` não estão em sequências completas: em alguns casos existe um registro para o mês de janeiro e depois registros para os meses de agosto em diante. Talvez isso explique a baixa quantidade de registros no período central do ano. 

O comportamento de um cliente fraudulento e de um cliente regular é visivelmente diferente em todas as visualizações criadas e analisadas. Várias outras visualizações ou combinações de atributos poderiam ser feitas para aprofundar os insights gerados. Escolhi não gerar tantas visualizações para que o documento não ficasse maior do que já está.

Quanto a abordagem que irei tomar: irei tratar os dados como parte de um problema de detecção de anomalias. Nessa base temos um caso ótimo. Um caso ótimo é onde se tem uma boa quantidade de dados rotulados. Nessa base existe uma quantidade considerável de dados rotulados que facilitam o enfrentamento do problema. O problema mostraria suas dificuldades caso a rotulação de fraudes fosse rara, existisse alguma quantidade de contaminação na base e as evidências do perfil dos clientes fraudulentos fossem mais subjetivas. As fraudes de boleto presentes nessa base são tão distintas do comportamento normal que, provavelmente, podem ser tratadas como um problema de classificação simples. Trarei também uma abordagem de detecção de anomalias que se baseia em uma rede neural e apresentou bons resultados em casos difíceis de detecção. Por fim, o objetivo é detectar um cliente fraudulento com base em sua atividade num período de tempo. Estou desconsiderando as lacunas temporais presentes nos meses de referencia, mas se houvesse uma continuidade poderia tentar usar um modelo de detecção que trabalhasse com séries temporais.

Como resultado, espero ter um modelo que consiga detectar clientes potencialmente fraudulentos, mitigando o problema das fraudes antes que ocorram ou sejam denunciadas.

## Salvar conjunto de dados resultante

In [77]:
data.to_csv('dataset_case_boleto_fe.csv', index=False)